# Class exercise: Suspended beams

3 beams are suspended on ropes A, B, C, D, E and G:

![](https://oit.tudelft.nl/CME4501/2024/_images/suspended_beams.svg)

Find the permissible total load which doesn’t exceed the maximum tension N in rope A and B, C and D, and E and G of respectively 300 N, 200 N and 100 N. What is the tension in the ropes for the permissible total load?

## Model

From mechanics it follows that:

$$
\begin{array}{l}
\sum {F_{\rm{v}}^{{\rm{EG}}}}  = 0 \to {N_E} + {N_G} - {F_2} = 0\\
\sum {T_{\rm{E}}^{{\rm{EG}}}}  = 0 \to 10{N_G} - {x_2}{F_2} = 0\\
\sum {F_{\rm{v}}^{{\rm{CD}}}}  = 0 \to {N_C} + {N_D} - {N_G} = 0\\
\sum {T_{\rm{C}}^{{\rm{CD}}}}  = 0 \to 8{N_D} - 6{N_G} = 0\\
\sum {F_{\rm{v}}^{{\rm{AB}}}}  = 0 \to {N_A} + {N_B} - {N_C} - {N_D} - {F_1} = 0\\
\sum {T_{\rm{A}}^{{\rm{AB}}}}  = 0 \to 10{N_B} - 10{N_D} - {F_1}{x_1} - 2{N_C} = 0
\end{array}
$$

The problem can be stated as follows:

$$
\begin{align}
&\underset{x}{\mathop{\min }}\left(-F_1-F_2\right) \\ 
& \text{with}   &x=\left[ \begin{matrix}
{{F_1}}\\
{{F_2}}\\
{{x_1}}\\
{{x_2}} \\
\end{matrix} \right] \\
&\text{such that} & N_A\left(F_1, F_2, x_1, x_2\right) \le 300 \\
&& N_B\left(F_1, F_2, x_1, x_2\right) \le 300 \\
&& N_C\left(F_1, F_2, x_1, x_2\right) \le 200 \\
&& N_D\left(F_1, F_2, x_1, x_2\right) \le 200 \\
&& N_E\left(F_1, F_2, x_1, x_2\right) \le 100 \\
&& N_G\left(F_1, F_2, x_1, x_2\right) \le 100 \\
&& 0 \le F_1 \\
&& 0 \le F_2 \\
&& 0 \le x_1 \le 10 \\
&& 0 \le x_2 \le 10  \\
\end{align}
$$

This could be solved by solving the systems of equations when evaluation the constraints, or solving the systems of equation symbolically on beforehand. In the second case, we can rephrase the model as:

$$
\begin{align}
&\underset{x}{\mathop{\min }}\left(-F_1-F_2\right) \\ 
& \text{with}   &x=\left[ \begin{matrix}
{{F_1}}\\
{{F_2}}\\
{{x_1}}\\
{{x_2}} \\
\end{matrix} \right] \\
&\text{such that} & - \cfrac{F_{1} x_{1}}{10} + F_{1} + \cfrac{F_{2} x_{2}}{50} \le 300 \\
&& \cfrac{F_{1} x_{1}}{10} + \cfrac{2 F_{2} x_{2}}{25} \le 300 \\
&& \cfrac{F_{2} x_{2}}{40} \le 200 \\
&& \cfrac{3 F_{2} x_{2}}{40} \le 200 \\
&& - \cfrac{F_{2} x_{2}}{10} + F_{2} \le 100 \\
&& \cfrac{F_{2} x_{2}}{10} \le 100 \\
&& 0 \le F_1 \\
&& 0 \le F_2 \\
&& 0 \le x_1 \le 10 \\
&& 0 \le x_2 \le 10  \\
\end{align}
$$

## Method

Now let's solve this problem using an optimization method.

In [1]:
import scipy as sp 
import numpy as np

In [2]:
x0 = np.array([500, 100, 2, 9])

In [3]:
def func(x):
    return -x[0] - x[1]

In [4]:
# solving the systems of equations during every iteration
def nonlinconfun(x):
    F_1 = x[0]
    F_2 = x[1]
    x_1 = x[2]
    x_2 = x[3]
    A = np.array([[0,0,0,0,1,1],
                  [0,0,0,0,0,10],
                  [0,0,1,1,0,-1],
                  [0,0,0,8,0,-6],
                  [1,1,-1,-1,0,0],
                  [0,10,-2,-10,0,0]])
    b = np.array([F_2, x_2*F_2, 0, 0, F_1, F_1*x_1])
    sol = np.linalg.solve(A,b)
    return sol

cons = sp.optimize.NonlinearConstraint(nonlinconfun, np.array([-np.inf,-np.inf,-np.inf,-np.inf,-np.inf,-np.inf]), np.array([300,300,200,200,100,100]))

In [5]:
bounds = [[0, None],
          [0, None],
          [0, 10],
          [0, 10]]

In [6]:
result = sp.optimize.minimize(fun = func, x0 = x0, bounds = bounds,constraints=cons)
print(result.fun)
print(result.x)
print(nonlinconfun(result.x))

-700.0000000000525
[549.95615294 150.04384706   4.7270118    3.33528152]
[300.         300.          12.51096176  37.53288529 100.
  50.04384706]


In [7]:
x0 = np.array([1000,1000,10,10])

In [8]:
result = sp.optimize.minimize(fun = func, x0 = x0, bounds = bounds,constraints=cons)
print(result.fun)
print(result.x)
print(nonlinconfun(result.x))

-700.0
[500.  200.    4.4   5. ]
[300. 300.  25.  75. 100. 100.]


We get different results for different initial guesses
- With initial guess: $F_1 = 500$, $F_2 = 100$, $x_1 = 2$, $x_2 = 9$:
  - Total permissible load $\approx 700$
  - $F_1 \approx 550$, $F_2 = 150$, $x_1 = 4.73$, $x_2 = 3.34$
  - $N_A = 300$, $N_B = 300$, $N_C \approx 12.5$, $N_D \approx 37.5$, $N_E \approx 100$, $N_G \approx 50.0$
- With initial guess: $F_1 = 1000$, $F_2 = 1000$, $x_1 = 10$, $x_2 = 10$:
  - Total permissible load $= 700$
  - $F_1 = 500$, $F_2 = 200$, $x_1 = 4.4$, $x_2 = 5$
  - $N_A = 300$, $N_B = 300$, $N_C \approx 25$, $N_D \approx 75$, $N_E \approx 100$, $N_G \approx 100.0$